<a href="https://colab.research.google.com/github/Anuj6005/Final_Proj/blob/main/Untitled1.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!git clone https://github.com/Atharva647/DAta.git


Cloning into 'DAta'...
remote: Enumerating objects: 53, done.
remote: Counting objects: 100% (3/3), done.
remote: Compressing objects: 100% (3/3), done.
remote: Total 53 (delta 0), reused 0 (delta 0), pack-reused 50 (from 1)
Receiving objects: 100% (53/53), 107.84 MiB | 39.10 MiB/s, done.


In [ ]:
pip install ultralytics


In [ ]:
pip install deep_sort_realtime

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.4/8.4 MB 41.1 MB/s eta 0:00:00


In [ ]:
import os
import numpy as np
import torch
import cv2
from ultralytics import YOLO
from PIL import Image
from tqdm import tqdm
from sklearn.model_selection import train_test_split
import shutil
from deep_sort_realtime.deepsort_tracker import DeepSort
import torch.nn as nn
from torch.utils.data import Dataset, DataLoader

Creating new Ultralytics Settings v0.0.6 file ✅ 
View Ultralytics Settings with 'yolo settings' or at '/root/.config/Ultralytics/settings.json'
Update Settings with 'yolo settings key=value', i.e. 'yolo settings runs_dir=path/to/dir'. For help see https://docs.ultralytics.com/quickstart/#ultralytics-settings.


In [ ]:
# Step 1: Load YOLO Model
model = YOLO("yolov8n.pt")  # Load YOLOv8 nano model

deep_sort_tracker = DeepSort(max_age=30, n_init=3, nn_budget=100)

100%|██████████| 6.25M/6.25M [00:00<00:00, 76.5MB/s]


In [ ]:
# Step 2: Extract Frames from Videos
def extract_frames(video_path, output_dir, frame_rate=5):
    os.makedirs(output_dir, exist_ok=True)
    cap = cv2.VideoCapture(video_path)
    frame_count = 0
    while cap.isOpened():
        success, frame = cap.read()
        if not success:
            break
        if frame_count % frame_rate == 0:
            frame_path = os.path.join(output_dir, f"frame{frame_count:04d}.jpg")
            cv2.imwrite(frame_path, frame)
        frame_count += 1
    cap.release()
    print(f"Frames saved to {output_dir}")


In [ ]:
# Step 3: Process Videos to Extract Frames
def process_videos(input_dir, output_dir, frame_rate=1):
    for label in os.listdir(input_dir):
        label_dir = os.path.join(input_dir, label)
        if not os.path.isdir(label_dir):
            continue
        output_label_dir = os.path.join(output_dir, label)
        os.makedirs(output_label_dir, exist_ok=True)
        for video_file in os.listdir(label_dir):
            if video_file.endswith(('.mp4', '.avi', '.mkv')):
                video_path = os.path.join(label_dir, video_file)
                output_video_dir = os.path.join(output_label_dir, os.path.splitext(video_file)[0])
                os.makedirs(output_video_dir, exist_ok=True)
                extract_frames(video_path, output_video_dir, frame_rate=frame_rate)

In [ ]:
# Example usage:
input_dir = r"/content/DAta/Data"
output_dir = "/content/Frames"
frame_rate = 1  # Save every frame
process_videos(input_dir, output_dir, frame_rate)

Frames saved to /content/Frames/Accident/V1
Frames saved to /content/Frames/Accident/V7
Frames saved to /content/Frames/Accident/V2
Frames saved to /content/Frames/Accident/V5
Frames saved to /content/Frames/Accident/V4
Frames saved to /content/Frames/Accident/collision_with_stationary_object_260
Frames saved to /content/Frames/Accident/side_collision_203
Frames saved to /content/Frames/Accident/V3
Frames saved to /content/Frames/Non acciden/negative_samples_136
Frames saved to /content/Frames/Non acciden/negative_samples_1096
Frames saved to /content/Frames/Non acciden/negative_samples_1097
Frames saved to /content/Frames/Non acciden/negative_samples_1108
Frames saved to /content/Frames/Non acciden/negative_samples_1093
Frames saved to /content/Frames/Non acciden/negative_samples_1095
Frames saved to /content/Frames/Non acciden/negative_samples_1110
Frames saved to /content/Frames/Non acciden/negative_samples_150
Frames saved to /content/Frames/Non acciden/negative_samples_1107
Frames

In [ ]:
frames_dir = r"/content/Frames"

In [ ]:
import os
import numpy as np
import torch
from ultralytics import YOLO
from PIL import Image

def extract_features_yolo(frame_path, model):
    """
    Extract YOLO features for a single frame.

    Args:
        frame_path (str): Path to the frame image.
        model: YOLO model object.

    Returns:
        np.ndarray: Array of features for the frame.
    """
    # Load the image
    img = Image.open(frame_path)
    img = np.array(img)  # Convert the image to a numpy array

    # Run inference using the YOLO model
    results = model(img)  # Make prediction on the image

    frame_features = []
    # Access the detections for the image
    for det in results[0].boxes:  # Iterate over detections in the result
        # Extract bounding box in xyxy format, class, and confidence
        x1, y1, x2, y2 = det.xyxy[0].tolist()
        conf = det.conf[0].item()
        cls = int(det.cls[0].item())
        frame_features.append([x1, y1, x2, y2, cls, conf])

    return np.array(frame_features)

In [ ]:
#main code
def track_objects_with_deepsort(frame, detections):
    tracked_objects = []

    # DeepSORT expects detections as [(bbox, confidence, class_id), ...]
    det_boxes = [[d[0], d[1], d[2], d[3]] for d in detections]  # Extract bbox
    scores = [d[4] for d in detections]  # Extract confidence scores
    class_ids = [d[5] for d in detections]  # Extract class IDs

    print(f"\n🔹 Processed Detections (Before DeepSORT): {list(zip(det_boxes, scores, class_ids))}")

    # Ensure detections are passed as (bbox, score, class_id)
    formatted_detections = [(det_boxes[i], scores[i], class_ids[i]) for i in range(len(det_boxes))]

    # Run DeepSORT tracker
    tracks = deep_sort_tracker.update_tracks(formatted_detections, None, frame)

    print(f"🔹 DeepSORT Output (Tracks): {tracks}")

    for track in tracks:
        if not track.is_confirmed() or track.time_since_update > 1:
            continue

        track_id = track.track_id
        bbox = track.to_tlbr()  # Convert bounding box format
        conf = track.det_conf  # Confidence score
        cls_id = track.det_class  # Class ID

        tracked_objects.append((track_id, *bbox, conf, cls_id))

    print(f"✅ Tracked Objects: {tracked_objects}")
    return tracked_objects


In [ ]:
import os

features_dir = "/content/Features"  # Adjust path if needed
os.makedirs(features_dir, exist_ok=True)

print(f"✅ Created Features Directory: {features_dir}")


✅ Created Features Directory: /content/Features


In [15]:
#main code
import os
import numpy as np
from PIL import Image

def process_video_frames_with_tracking(frame_dir, output_dir, model):
    os.makedirs(output_dir, exist_ok=True)

    for category in os.listdir(frame_dir):  # Loop through 'Accident' and 'Non accident' folders
        category_path = os.path.join(frame_dir, category)

        if not os.path.isdir(category_path):  # Skip files, process only directories
            continue

        output_category_dir = os.path.join(output_dir, category)
        os.makedirs(output_category_dir, exist_ok=True)

        for video_folder in os.listdir(category_path):  # Each video has its own folder
            video_path = os.path.join(category_path, video_folder)

            if not os.path.isdir(video_path):
                continue  # Skip files, process only directories

            output_video_dir = os.path.join(output_category_dir, video_folder)
            os.makedirs(output_video_dir, exist_ok=True)

            for frame_name in sorted(os.listdir(video_path)):  # Process each frame inside the video folder
                frame_path = os.path.join(video_path, frame_name)

                if frame_path.lower().endswith(('png', 'jpg', 'jpeg')):
                    img = np.array(Image.open(frame_path))

                    # Run YOLO
                    results = model(img)
                    detections = [[*det.xyxy[0].tolist(), det.conf[0].item(), int(det.cls[0].item())] for det in results[0].boxes]

                    print(f"\n🔹 Frame: {frame_name} (Category: {category}, Video: {video_folder})")
                    print(f"YOLO Detections: {detections}")

                    # Run DeepSORT
                    tracked_objects = track_objects_with_deepsort(img, detections)

                    print(f"Tracked Objects: {tracked_objects}")

                    # Save only if objects are tracked
                    if tracked_objects:
                        np.save(os.path.join(output_video_dir, frame_name.replace('.jpg', '.npy')), np.array(tracked_objects))
                        print(f"✅ Saved: {frame_name.replace('.jpg', '.npy')}")

# **Re-run the function**
process_video_frames_with_tracking(frames_dir, features_dir, model)


Streaming output truncated to the last 5000 lines.
🔹 DeepSORT Output (Tracks): [<deep_sort_realtime.deep_sort.track.Track object at 0x7aa43c616090>, <deep_sort_realtime.deep_sort.track.Track object at 0x7aa43c60df90>, <deep_sort_realtime.deep_sort.track.Track object at 0x7aa44ea0c9d0>, <deep_sort_realtime.deep_sort.track.Track object at 0x7aa43c617590>, <deep_sort_realtime.deep_sort.track.Track object at 0x7aa44eaa2310>, <deep_sort_realtime.deep_sort.track.Track object at 0x7aa44eaa3910>, <deep_sort_realtime.deep_sort.track.Track object at 0x7aa43c615950>, <deep_sort_realtime.deep_sort.track.Track object at 0x7aa43c60c950>, <deep_sort_realtime.deep_sort.track.Track object at 0x7aa43c617b50>, <deep_sort_realtime.deep_sort.track.Track object at 0x7aa43c60db10>, <deep_sort_realtime.deep_sort.track.Track object at 0x7aa44ea1af10>, <deep_sort_realtime.deep_sort.track.Track object at 0x7aa44ea254d0>, <deep_sort_realtime.deep_sort.track.Track object at 0x7aa44ea26810>, <deep_sort_realtime.dee

In [16]:
import os

# **Frame Extraction Directory**
frames_dir = "/content/Frames"  # Where extracted frames from videos are stored

# **YOLO + DeepSORT Features Directory**
features_dir = "/content/Features"  # Stores tracked objects as .npy files

# **LSTM Sequence Directory**
sequences_dir = "/content/LSTM_Sequences"  # Stores processed sequences for LSTM training

# **Ensure directories exist**
os.makedirs(frames_dir, exist_ok=True)
os.makedirs(features_dir, exist_ok=True)
os.makedirs(sequences_dir, exist_ok=True)

print("✅ Directory setup complete:")
print(f"Frames Directory: {frames_dir}")
print(f"Features Directory: {features_dir}")
print(f"Sequences Directory: {sequences_dir}")


✅ Directory setup complete:
Frames Directory: /content/Frames
Features Directory: /content/Features
Sequences Directory: /content/LSTM_Sequences


In [17]:
import os
import numpy as np

def prepare_sequences(features_dir, sequence_length=10, output_dir="/content/LSTM_Sequences"):
    """
    Converts YOLO + DeepSORT feature files (.npy) into sequences for LSTM training.
    Handles empty feature files, nested folders, and non-numeric data.
    """
    os.makedirs(output_dir, exist_ok=True)

    # Collect all .npy files from nested directories
    feature_files = []
    for root, _, files in os.walk(features_dir):
        for file in files:
            if file.endswith(".npy"):
                feature_files.append(os.path.join(root, file))

    if not feature_files:
        raise FileNotFoundError("No .npy files found in the directory structure!")

    for feature_path in sorted(feature_files):
        print(f"Processing: {feature_path}")

        try:
            features = np.load(feature_path, allow_pickle=True)

            # Check if features are a valid NumPy array
            if not isinstance(features, np.ndarray):
                print(f"⚠️ Skipping {feature_path}: Invalid data type {type(features)}")
                continue

            # Ensure data is numeric
            if not np.issubdtype(features.dtype, np.number):
                print(f"⚠️ Skipping {feature_path}: Contains non-numeric data")
                continue

            # Ensure enough data for sequences
            if len(features) < sequence_length:
                print(f"⚠️ Skipping {feature_path}: Not enough frames for a sequence")
                continue  # Avoid errors when slicing

            # Create output directory for each video
            relative_path = os.path.relpath(feature_path, features_dir)
            video_output_dir = os.path.join(output_dir, os.path.dirname(relative_path))
            os.makedirs(video_output_dir, exist_ok=True)

            # Generate sequences
            for i in range(len(features) - sequence_length + 1):
                sequence = features[i:i + sequence_length]
                sequence_filename = os.path.join(video_output_dir, f"{os.path.basename(feature_path).replace('.npy', '')}_seq_{i}.npy")
                np.save(sequence_filename, sequence.astype(np.float32))  # Convert to numeric type

            print(f"✅ Sequences saved for {feature_path}")

        except Exception as e:
            print(f"❌ Error processing {feature_path}: {str(e)}")

    print("🎉 Sequence preparation complete!")

# **Call the function**
prepare_sequences(features_dir, sequence_length=10, output_dir=sequences_dir)


Streaming output truncated to the last 5000 lines.
⚠️ Skipping /content/Features/Non acciden/negative_samples_133/frame0150.npy: Contains non-numeric data
Processing: /content/Features/Non acciden/negative_samples_133/frame0151.npy
⚠️ Skipping /content/Features/Non acciden/negative_samples_133/frame0151.npy: Contains non-numeric data
Processing: /content/Features/Non acciden/negative_samples_133/frame0152.npy
⚠️ Skipping /content/Features/Non acciden/negative_samples_133/frame0152.npy: Contains non-numeric data
Processing: /content/Features/Non acciden/negative_samples_133/frame0153.npy
⚠️ Skipping /content/Features/Non acciden/negative_samples_133/frame0153.npy: Contains non-numeric data
Processing: /content/Features/Non acciden/negative_samples_133/frame0154.npy
⚠️ Skipping /content/Features/Non acciden/negative_samples_133/frame0154.npy: Contains non-numeric data
Processing: /content/Features/Non acciden/negative_samples_133/frame0155.npy
⚠️ Skipping /content/Features/Non acciden/ne

In [21]:
print("Sequences Directory:", os.listdir(sequences_dir) if os.path.exists(sequences_dir) else "No sequences found")


Sequences Directory: ['Accident', 'Non acciden']


In [19]:
import os

for root, dirs, files in os.walk(features_dir):
    print(f"\n📂 Directory: {root}")
    print(f"📄 Files: {files}")



📂 Directory: /content/Features
📄 Files: []

📂 Directory: /content/Features/Accident
📄 Files: []

📂 Directory: /content/Features/Accident/V7
📄 Files: ['frame0045.npy', 'frame0114.npy', 'frame0281.npy', 'frame0348.npy', 'frame0128.npy', 'frame0349.npy', 'frame0063.npy', 'frame0157.npy', 'frame0264.npy', 'frame0198.npy', 'frame0009.npy', 'frame0108.npy', 'frame0336.npy', 'frame0016.npy', 'frame0197.npy', 'frame0280.npy', 'frame0330.npy', 'frame0342.npy', 'frame0127.npy', 'frame0117.npy', 'frame0167.npy', 'frame0078.npy', 'frame0112.npy', 'frame0143.npy', 'frame0037.npy', 'frame0238.npy', 'frame0158.npy', 'frame0147.npy', 'frame0320.npy', 'frame0298.npy', 'frame0073.npy', 'frame0013.npy', 'frame0069.npy', 'frame0151.npy', 'frame0054.npy', 'frame0119.npy', 'frame0300.npy', 'frame0137.npy', 'frame0149.npy', 'frame0050.npy', 'frame0095.npy', 'frame0200.npy', 'frame0029.npy', 'frame0221.npy', 'frame0333.npy', 'frame0036.npy', 'frame0142.npy', 'frame0201.npy', 'frame0205.npy', 'frame0100.npy',

In [20]:
def prepare_sequences(features_dir, sequence_length=10, output_dir="/content/LSTM_Sequences"):
    os.makedirs(output_dir, exist_ok=True)

    feature_files = []
    for root, _, files in os.walk(features_dir):
        for file in files:
            if file.endswith(".npy"):
                feature_files.append(os.path.join(root, file))

    if not feature_files:
        print("⚠️ No .npy files found in features directory!")
        return  # Stop execution

    for feature_path in sorted(feature_files):
        print(f"\n🔹 Processing: {feature_path}")

        try:
            features = np.load(feature_path, allow_pickle=True)
            print(f"📊 Loaded Features Shape: {features.shape}")

            if not isinstance(features, np.ndarray):
                print(f"⚠️ Skipping {feature_path}: Invalid data type {type(features)}")
                continue

            if len(features) < sequence_length:
                print(f"⚠️ Skipping {feature_path}: Not enough frames for a sequence")
                continue

            relative_path = os.path.relpath(feature_path, features_dir)
            video_output_dir = os.path.join(output_dir, os.path.dirname(relative_path))
            os.makedirs(video_output_dir, exist_ok=True)

            for i in range(len(features) - sequence_length + 1):
                sequence = features[i:i + sequence_length]
                sequence_filename = os.path.join(video_output_dir, f"{os.path.basename(feature_path).replace('.npy', '')}_seq_{i}.npy")
                np.save(sequence_filename, sequence.astype(np.float32))

            print(f"✅ Sequences saved for {feature_path}")

        except Exception as e:
            print(f"❌ Error processing {feature_path}: {str(e)}")

    print("🎉 Sequence preparation complete!")

# **Re-run the function**
prepare_sequences(features_dir, sequence_length=10, output_dir=sequences_dir)


Streaming output truncated to the last 5000 lines.
🔹 Processing: /content/Features/Non acciden/negative_samples_145/frame0076.npy
📊 Loaded Features Shape: (14, 7)
✅ Sequences saved for /content/Features/Non acciden/negative_samples_145/frame0076.npy

🔹 Processing: /content/Features/Non acciden/negative_samples_145/frame0077.npy
📊 Loaded Features Shape: (14, 7)
✅ Sequences saved for /content/Features/Non acciden/negative_samples_145/frame0077.npy

🔹 Processing: /content/Features/Non acciden/negative_samples_145/frame0078.npy
📊 Loaded Features Shape: (14, 7)
✅ Sequences saved for /content/Features/Non acciden/negative_samples_145/frame0078.npy

🔹 Processing: /content/Features/Non acciden/negative_samples_145/frame0079.npy
📊 Loaded Features Shape: (14, 7)
✅ Sequences saved for /content/Features/Non acciden/negative_samples_145/frame0079.npy

🔹 Processing: /content/Features/Non acciden/negative_samples_145/frame0080.npy
📊 Loaded Features Shape: (13, 7)
✅ Sequences saved for /content/Featur

In [22]:
import os
import shutil
from sklearn.model_selection import train_test_split

def split_data(sequences_dir, output_dir, train_ratio=0.7, val_ratio=0.15, test_ratio=0.15):
    """
    Split sequences into training, validation, and test sets.

    Args:
        sequences_dir (str): Directory containing sequences.
        output_dir (str): Directory to save split datasets.
        train_ratio (float): Ratio of data for training.
        val_ratio (float): Ratio of data for validation.
        test_ratio (float): Ratio of data for testing.
    """
    assert train_ratio + val_ratio + test_ratio == 1.0, "Ratios must sum to 1.0"
    os.makedirs(output_dir, exist_ok=True)

    # Create subdirectories for train, val, and test
    splits = ['train', 'val', 'test']
    for split in splits:
        split_dir = os.path.join(output_dir, split)
        os.makedirs(split_dir, exist_ok=True)

    for label in os.listdir(sequences_dir):
        label_dir = os.path.join(sequences_dir, label)
        if not os.path.isdir(label_dir):
            continue

        sequences = []
        for video_name in os.listdir(label_dir):
            video_dir = os.path.join(label_dir, video_name)
            if os.path.isdir(video_dir):
                sequences.append(video_dir)

        # Split the data
        train_data, temp_data = train_test_split(sequences, test_size=(1 - train_ratio), random_state=42)
        val_data, test_data = train_test_split(temp_data, test_size=(test_ratio / (val_ratio + test_ratio)), random_state=42)

        # Copy sequences to respective directories
        for split_name, split_data in zip(splits, [train_data, val_data, test_data]):
            split_label_dir = os.path.join(output_dir, split_name, label)
            os.makedirs(split_label_dir, exist_ok=True)
            for video_dir in split_data:
                shutil.copytree(video_dir, os.path.join(split_label_dir, os.path.basename(video_dir)))

        print(f"Data split completed for label: {label}")

# Set Directories
sequences_dir = "/content/LSTM_Sequences"  # Directory with prepared sequences
output_dir = "Dataset_Split"  # Directory to save split data

# Split Data
split_data(sequences_dir, output_dir)


ValueError: With n_samples=1, test_size=0.5 and train_size=None, the resulting train set will be empty. Adjust any of the aforementioned parameters.

In [23]:
import os
import shutil
from sklearn.model_selection import train_test_split

def split_data(sequences_dir, output_dir, train_ratio=0.7, val_ratio=0.15, test_ratio=0.15):
    """
    Split sequences into training, validation, and test sets while handling all possible sequence sizes.

    Args:
        sequences_dir (str): Directory containing sequences.
        output_dir (str): Directory to save split datasets.
        train_ratio (float): Ratio of data for training.
        val_ratio (float): Ratio of data for validation.
        test_ratio (float): Ratio of data for testing.
    """
    assert train_ratio + val_ratio + test_ratio == 1.0, "Ratios must sum to 1.0"
    os.makedirs(output_dir, exist_ok=True)

    # Create subdirectories for train, val, and test
    splits = ['train', 'val', 'test']
    for split in splits:
        os.makedirs(os.path.join(output_dir, split), exist_ok=True)

    for label in os.listdir(sequences_dir):
        label_dir = os.path.join(sequences_dir, label)
        if not os.path.isdir(label_dir):
            continue

        sequences = [os.path.join(label_dir, vid) for vid in os.listdir(label_dir) if os.path.isdir(os.path.join(label_dir, vid))]

        if len(sequences) == 0:
            print(f"Skipping label '{label}': No sequences found.")
            continue
        elif len(sequences) == 1:
            print(f"Only one sequence for label '{label}', assigning to training set.")
            train_data, val_data, test_data = sequences, [], []
        elif len(sequences) == 2:
            print(f"Two sequences for label '{label}', assigning one to training, one to validation.")
            train_data, val_data, test_data = train_test_split(sequences, test_size=0.5, random_state=42), [], []
        elif len(sequences) == 3:
            print(f"Three sequences for label '{label}', assigning one to each set.")
            train_data, val_data, test_data = sequences[:1], sequences[1:2], sequences[2:]
        else:
            train_data, temp_data = train_test_split(sequences, test_size=(1 - train_ratio), random_state=42)
            val_data, test_data = train_test_split(temp_data, test_size=(test_ratio / (val_ratio + test_ratio)), random_state=42)

        # Copy sequences to respective directories
        for split_name, split_data in zip(splits, [train_data, val_data, test_data]):
            split_label_dir = os.path.join(output_dir, split_name, label)
            os.makedirs(split_label_dir, exist_ok=True)
            for video_dir in split_data:
                shutil.copytree(video_dir, os.path.join(split_label_dir, os.path.basename(video_dir)))

        print(f"Data split completed for label: {label}")

# Set Directories
sequences_dir = "/content/LSTM_Sequences"  # Directory with prepared sequences
output_dir = "Dataset_Split"  # Directory to save split data

# Split Data
split_data(sequences_dir, output_dir)


Three sequences for label 'Accident', assigning one to each set.
Data split completed for label: Accident
Data split completed for label: Non acciden


In [34]:
import torch
import torch.nn as nn
from torch.utils.data import Dataset, DataLoader
import os
import numpy as np

class AccidentDataset(Dataset):
    def __init__(self, data_dir, max_detections=20, feature_size=6):
        self.data = []
        self.labels = []
        self.max_detections = max_detections
        self.feature_size = feature_size
        self.classes = sorted(os.listdir(data_dir))

        for label, class_name in enumerate(self.classes):
            class_dir = os.path.join(data_dir, class_name)
            for video_name in os.listdir(class_dir):
                video_dir = os.path.join(class_dir, video_name)
                for sequence_file in os.listdir(video_dir):
                    if sequence_file.endswith('.npy'):
                        sequence_path = os.path.join(video_dir, sequence_file)
                        self.data.append(sequence_path)
                        self.labels.append(label)

    def __len__(self):
        return len(self.data)

    def __getitem__(self, idx):
        sequence_path = self.data[idx]
        label = self.labels[idx]

        # Load the sequence with allow_pickle=True
        sequence = np.load(sequence_path, allow_pickle=True)

        # Process each frame in the sequence
        processed_sequence = []
        for frame_features in sequence:
            frame_features = np.array(frame_features, dtype=np.float32)

            # Ensure frame_features is always 2D
            if frame_features.ndim == 1:
                frame_features = np.expand_dims(frame_features, axis=0)  # Convert (feature_size,) → (1, feature_size)
            elif frame_features.ndim == 0:
                frame_features = np.zeros((1, self.feature_size), dtype=np.float32)  # Handle empty detections


            # Ensure all frames have the expected feature size
            if frame_features.shape[1] != self.feature_size:
                print(f"Warning: Feature size mismatch in {sequence_path}. Expected {self.feature_size}, got {frame_features.shape[1]}. Fixing...")
                frame_features = frame_features[:, :self.feature_size]  # Trim excess features

            # Handle empty detections
            #if len(frame_features) == 0:
                #frame_features = np.zeros((1, self.feature_size), dtype=np.float32)

            # Pad or truncate to match max_detections
            if len(frame_features) > self.max_detections:
                frame_features = frame_features[:self.max_detections]
            elif len(frame_features) < self.max_detections:
                padding = np.zeros((self.max_detections - len(frame_features), self.feature_size), dtype=np.float32)
                frame_features = np.vstack((frame_features, padding))

            # Flatten the frame features
            flattened_features = frame_features.flatten()
            processed_sequence.append(flattened_features)

        # Convert processed sequence to a tensor
        processed_sequence = np.array(processed_sequence, dtype=np.float32)
        processed_sequence = torch.tensor(processed_sequence, dtype=torch.float32)

        return processed_sequence, label


In [35]:
# Step 7: Define LSTM Model
class AccidentLSTM(nn.Module):
    def __init__(self, input_size, hidden_size, num_layers, num_classes):
        super(AccidentLSTM, self).__init__()
        self.lstm = nn.LSTM(input_size, hidden_size, num_layers, batch_first=True)
        self.fc = nn.Linear(hidden_size, num_classes)
    def forward(self, x):
        _, (hidden, _) = self.lstm(x)
        return self.fc(hidden[-1])


In [36]:
# Step 8: Train LSTM Model
def train_model(model, dataloaders, criterion, optimizer, num_epochs, device):
    model = model.to(device)
    for epoch in range(num_epochs):
        print(f"Epoch {epoch + 1}/{num_epochs}\n" + "-" * 20)
        for phase in ['train', 'val']:
            model.train() if phase == 'train' else model.eval()
            running_loss, correct_predictions = 0.0, 0
            for sequences, labels in dataloaders[phase]:
                sequences, labels = sequences.to(device), labels.to(device)
                optimizer.zero_grad()
                with torch.set_grad_enabled(phase == 'train'):
                    outputs = model(sequences)
                    loss = criterion(outputs, labels)
                    _, preds = torch.max(outputs, 1)
                    if phase == 'train':
                        loss.backward()
                        optimizer.step()
                running_loss += loss.item() * sequences.size(0)
                correct_predictions += torch.sum(preds == labels.data)
            print(f"{phase.capitalize()} Loss: {running_loss / len(dataloaders[phase].dataset):.4f} Acc: {correct_predictions.double() / len(dataloaders[phase].dataset):.4f}")
    print("Training complete")
    return model


In [37]:
# Data Loaders
batch_size = 16
data_dir = "/content/Dataset_Split"

datasets = {phase: AccidentDataset(os.path.join(data_dir, phase)) for phase in ['train', 'val']}
dataloaders = {phase: DataLoader(datasets[phase], batch_size=batch_size, shuffle=True) for phase in ['train', 'val']}

# Model Parameters
input_size = 120  # x1, y1, x2, y2, class, confidence
hidden_size = 128
num_layers = 2
num_classes = len(os.listdir(os.path.join(data_dir, 'train')))
num_epochs = 20
learning_rate = 0.001

# Instantiate Model, Loss, and Optimizer
model = AccidentLSTM(input_size, hidden_size, num_layers, num_classes)
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate)

# Device Configuration
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

# Train the Model
trained_model = train_model(model, dataloaders, criterion, optimizer, num_epochs, device)


Streaming output truncated to the last 5000 lines.
Val Loss: nan Acc: 0.0275
Training complete
